In [18]:
import pandas as pd
import numpy as np

In [19]:
listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls'], axis=1, inplace=True)

In [20]:
listing_details.shape[0]

32461

In [21]:
listing_details_cleaned = pd.read_csv('output/listing_details_cleaned.csv')
listing_details_cleaned.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27246 entries, 0 to 27245
Data columns (total 29 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Tỉnh/Thành phố                        27246 non-null  object 
 1   Thành phố/Quận/Huyện/Thị xã           27246 non-null  object 
 2   Xã/Phường/Thị trấn                    26947 non-null  object 
 3   Đường phố                             20229 non-null  object 
 4   Chi tiết                              27246 non-null  object 
 5   Nguồn thông tin                       27246 non-null  object 
 6   Tình trạng giao dịch                  27246 non-null  object 
 7   Thời điểm giao dịch/rao bán           27236 non-null  object 
 8   Thông tin liên hệ                     0 non-null      float64
 9   Giá rao bán/giao dịch                 24742 non-null  float64
 10  Loại đơn giá (đ/m2 hoặc đ/m ngang)    27246 non-null  object 
 11  Số tầng công tr

In [22]:
listing_details_cleaned.rename(columns={'Nguồn thông tin': 'url'}, inplace=True)
listing_details_cleaned.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27246 entries, 0 to 27245
Data columns (total 29 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Tỉnh/Thành phố                        27246 non-null  object 
 1   Thành phố/Quận/Huyện/Thị xã           27246 non-null  object 
 2   Xã/Phường/Thị trấn                    26947 non-null  object 
 3   Đường phố                             20229 non-null  object 
 4   Chi tiết                              27246 non-null  object 
 5   url                                   27246 non-null  object 
 6   Tình trạng giao dịch                  27246 non-null  object 
 7   Thời điểm giao dịch/rao bán           27236 non-null  object 
 8   Thông tin liên hệ                     0 non-null      float64
 9   Giá rao bán/giao dịch                 24742 non-null  float64
 10  Loại đơn giá (đ/m2 hoặc đ/m ngang)    27246 non-null  object 
 11  Số tầng công tr

In [23]:
cleaned = pd.merge(listing_details_cleaned, listing_details, how='left', on='url')
cleaned.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27248 entries, 0 to 27247
Data columns (total 35 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Tỉnh/Thành phố                        27248 non-null  object 
 1   Thành phố/Quận/Huyện/Thị xã           27248 non-null  object 
 2   Xã/Phường/Thị trấn                    26949 non-null  object 
 3   Đường phố                             20231 non-null  object 
 4   Chi tiết                              27248 non-null  object 
 5   url                                   27248 non-null  object 
 6   Tình trạng giao dịch                  27248 non-null  object 
 7   Thời điểm giao dịch/rao bán           27238 non-null  object 
 8   Thông tin liên hệ                     0 non-null      float64
 9   Giá rao bán/giao dịch                 24744 non-null  float64
 10  Loại đơn giá (đ/m2 hoặc đ/m ngang)    27248 non-null  object 
 11  Số tầng công tr

## Columns to fix: 

- Thành phố/Quận/Huyện/Thị xã (Xong)
- Xã/Phường/Thị trấn (xong)
- Giá rao bán/giao dịch (Không check nữa)

Đường phố, Số tầng công trình, Tổng diện tích sàn, Đơn giá xây dựng, Chất lượng còn lại, Diện tích đất (m2), Kích thước mặt tiền (m), Kích thước chiều dài (m), Số mặt tiền tiếp giáp, Hình dạng, Độ rộng ngõ/ngách nhỏ nhất (m), Khoảng cách tới trục đường chính (m)

# Test district from here

In [1]:
import argparse
import os
from datetime import date
import threading
from concurrent.futures import ThreadPoolExecutor, as_completed

import pandas as pd
import numpy as np

from src.selenium_manager import create_stealth_driver
from src.scraping import Scraper
from src.cleaning import DataCleaner, drop_mixed_listings, is_land_only
from src.feature_engineering import FeatureEngineer
from src.address_standardizer import AddressStandardizer
from src import config
from src.utils import save_urls_to_csv, save_details_to_csv, chunks
from src.tasks import scrape_worker
from src.modelling import predict_alley_width

def run_cleaning_pipeline():
    """Step 3: Clean the raw data and structure it."""
    if not os.path.exists(config.DETAILS_OUTPUT_FILE):
        print(f"Raw details file not found: {config.DETAILS_OUTPUT_FILE}. Run with `--mode details` first.")
        return

    print(f"Reading raw data from '{config.DETAILS_OUTPUT_FILE}'...")
    df_raw = pd.read_csv(config.DETAILS_OUTPUT_FILE)
    df_raw = drop_mixed_listings(df_raw)

    cleaned_records = []
    for _, row in df_raw.iterrows():
        row_dict = row.to_dict()
        direct_features = DataCleaner.extract_direct_features(row_dict)

        # --- 1. Detect if it is a land-only property ---
        is_land = is_land_only(row_dict)

        # --- 2. Extract all data ---
        processed_data = {
            'Tỉnh/Thành phố': DataCleaner.extract_city(row_dict),
            'Thành phố/Quận/Huyện/Thị xã': DataCleaner.extract_district(row_dict),
            'Xã/Phường/Thị trấn': DataCleaner.extract_ward(row_dict),
            'Đường phố': DataCleaner.extract_street(row_dict),
            'Chi tiết': DataCleaner.extract_address_detail(row_dict),
            'Nguồn thông tin': row_dict.get('url'),
            'Tình trạng giao dịch': 'Rao bán',
            'Thời điểm giao dịch/rao bán': DataCleaner.extract_published_date(row_dict.get('main_info')),
            'Thông tin liên hệ': None,
            'Giá rao bán/giao dịch': DataCleaner.extract_total_price(row_dict.get('main_info')),
            'Loại đơn giá (đ/m2 hoặc đ/m ngang)': 'đ/m2',
            'Số tầng công trình': DataCleaner.extract_num_floors(row_dict),
            'Tổng diện tích sàn': DataCleaner.extract_built_area(row_dict),
            'Đơn giá xây dựng': DataCleaner.get_construction_cost(row_dict),
            'Năm xây dựng': None,
            'Chất lượng còn lại': DataCleaner.estimate_remaining_quality(row_dict),
            'Diện tích đất (m2)': DataCleaner.extract_total_area(row_dict),
            'Kích thước mặt tiền (m)': DataCleaner.extract_facade_width(row_dict),
            'Kích thước chiều dài (m)': DataCleaner.extract_land_length(row_dict),
            'Số mặt tiền tiếp giáp': DataCleaner.extract_facade_count(row_dict),
            'Hình dạng': DataCleaner.extract_land_shape(row_dict),
            'Độ rộng ngõ/ngách nhỏ nhất (m)': DataCleaner.extract_alley_width(row_dict),
            'Khoảng cách tới trục đường chính (m)': DataCleaner.extract_distance_to_main_road(row_dict),
            'Mục đích sử dụng đất': 'Đất ở',
            'Yếu tố khác': " | ".join(direct_features) if direct_features else None,
            'Tọa độ (vĩ độ)': row_dict.get('latitude'),
            'Tọa độ (kinh độ)': row_dict.get('longitude'),
            'Hình ảnh của bài đăng': row_dict.get('image_urls'),
            'description': row_dict.get('description'),
            'is_land': is_land  # <-- Add the temporary flag here
        }

        # --- 3. Apply special logic if it's land only ---
        if is_land:
            processed_data['Số tầng công trình'] = 0
            processed_data['Đơn giá xây dựng'] = 0
            processed_data['Tổng diện tích sàn'] = 0
            processed_data['Chất lượng còn lại'] = 0
        
        cleaned_records.append(processed_data)

    df_cleaned = pd.DataFrame(cleaned_records)

    try:
        # Standardize Province and District using the simplified AddressStandardizer
        address_std = AddressStandardizer(
            config.PROVINCES_SQL_FILE,
            config.DISTRICTS_SQL_FILE,
            config.WARDS_SQL_FILE,
            config.STREETS_SQL_FILE
        )
        df_cleaned['Tỉnh/Thành phố'] = df_cleaned['Tỉnh/Thành phố'].apply(address_std.standardize_province)
        df_cleaned['short_address'] = df_raw['short_address']
        df_cleaned['Thành phố/Quận/Huyện/Thị xã'] = df_cleaned.apply(address_std.standardize_district, axis=1)
        df_cleaned['Xã/Phường/Thị trấn'] = df_cleaned.apply(address_std.standardize_ward, axis = 1)
        df_cleaned.drop(columns=['short_address'], inplace = True)
        return df_cleaned
        # df_cleaned['Thành phố/Quận/Huyện/Thị xã'] = df_cleaned.apply(address_std.standardize_district, axis=1)
        # df_cleaned.drop(columns=['short_address'], inplace=True)
        # print("Province and District standardization complete.")
    except FileNotFoundError:
        print("Skipping province/district standardization because data files were not found.")

cleaned = run_cleaning_pipeline()

Reading raw data from 'output/listing_details.csv'...
Removed 4972 listings containing 'thổ cư'.
Error parsing price: local variable 'cleaned_num' referenced before assignment


In [ ]:
# from src.address_standardizer import AddressStandardizer
from src import config
import sqlite3
import pandas as pd
from unicodedata import normalize
from rapidfuzz import fuzz

conn = sqlite3.connect(":memory:")
conn.execute("CREATE TABLE provinces (name TEXT, code TEXT, status TEXT);")
conn.execute("CREATE TABLE districts (name TEXT, code TEXT, province_code TEXT, status TEXT);")
conn.execute("CREATE TABLE wards (name TEXT, code TEXT, district_code TEXT, status TEXT);")
conn.execute("CREATE TABLE streets (name TEXT, code TEXT, district_code TEXT, status TEXT);")

with open(config.PROVINCES_SQL_FILE, "r", encoding="utf-8") as f:
    conn.executescript(f.read())

with open(config.DISTRICTS_SQL_FILE, "r", encoding="utf-8") as f:
    dis_cleaned = f.read().replace("\\'", "''")
    conn.executescript(dis_cleaned)

with open(config.WARDS_SQL_FILE, "r", encoding="utf-8") as f:
    ward_cleaned = f.read().replace("\\'", "''")
    conn.executescript(ward_cleaned)

provinces_df = pd.read_sql_query("SELECT * FROM provinces", conn)
districts_df = pd.read_sql_query("""
    SELECT d.name AS district_name, p.name AS province_name
    FROM districts d
    JOIN provinces p ON d.province_code = p.code
    """, conn)

wards_df = pd.read_sql_query("""
    SELECT w.name AS ward_name,
        d.name AS district_name,
        p.name AS province_name
    FROM wards w
    JOIN districts d ON w.district_code = d.code
    JOIN provinces p ON d.province_code = p.code
""", conn)

if 'conn' in locals():
    conn.close()

reverse_province_map = {
    prov.replace("Thành phố ", "").replace("Tỉnh ", ""): prov
    for prov in provinces_df['name'].unique()
}

reverse_district = {}
for province in districts_df['province_name'].unique():
    reverse_district[province] = {}
    for district_name in districts_df[districts_df['province_name'] == province]['district_name'].unique():
        district_name_strip = district_name.replace('Thành phố ', '').replace('Thành Phố ', '').replace('Quận ', '').replace('Huyện ', '').replace('Thị xã ', '').replace('Thị Xã ', '').strip()
        reverse_district[province][district_name_strip] = district_name
reverse_district['Tỉnh Bà Rịa - Vũng Tàu']['Long Đất'] = 'Huyện Long Đất'
reverse_district['Thành phố Hồ Chí Minh']['Quận 2'] = 'Thành phố Thủ Đức'
reverse_district['Thành phố Hồ Chí Minh']['Quận 9'] = 'Thành phố Thủ Đức'

# for province in districts_df['province_name'].unique():
#     reverse_district[province] = {}
#     for district_name in districts_df[districts_df['province_name'] == province]['district_name'].unique():
#         # district_name_strip = normalize('NFKD', district_name.replace('Thành phố ', '').replace('Thành Phố ', '').replace('Quận ', '').replace('Huyện ', '').replace('Thị xã ', '').replace('Thị Xã ', '').strip())
#         district_name_strip = district_name.replace('Thành phố ', '').replace('Thành Phố ', '').replace('Quận ', '').replace('Huyện ', '').replace('Thị xã ', '').replace('Thị Xã ', '').strip()
#         reverse_district[province][district_name_strip] = district_name
# reverse_district['Tỉnh Bà Rịa - Vũng Tàu']['Long Đất'] = 'Huyện Long Đất'

reverse_ward = {}
for province in reverse_district.keys():
    reverse_ward[province] = {}
    for district in reverse_district[province].values():
        reverse_ward[province][district] = {}
        for ward in wards_df[wards_df['district_name'] == district]['ward_name'].unique():
            ward_name_strip = normalize('NFC', ward.replace('Xã ', '').replace('Phường ', '').replace('Thị trấn ', '').replace('Thị Trấn ', '').strip())
            reverse_ward[province][district][ward_name_strip] = ward
# for district in wards_df['district_name'].unique():
#     reverse_ward[district] = {}
#     for ward_name in wards_df[wards_df['district_name'] == district]['ward_name'].unique():
#         ward_name_strip = normalize('NFKD', ward_name.replace('Xã ', '').replace('Phường ', '').replace('Thị trấn ', '').replace('Thị Trấn ', '').strip())
#         reverse_ward[district][ward_name_strip] = ward_name

def standardize_district(row):
        prefix = ['Thành phố', 'Thành Phố', 'Quận', 'Huyện', 'Thị xã', 'Thị Xã', 'Đảo']
        district_value = row['Thành phố/Quận/Huyện/Thị xã']
        if isinstance(district_value, str):
            for pre in prefix:
                if district_value.startswith(pre):
                    return district_value
            province = row['Tỉnh/Thành phố']
            if district_value in reverse_district[province].keys():
                return reverse_district[province][district_value]
            for dis in reverse_district[province].keys():
                similarity = fuzz.ratio(district_value, dis)
                if similarity >= 66:
                    print(f'Value: {district_value}')
                    print(f"Short address: {row['short_address']}")
                    print(f"Predicted value: {reverse_district[province][dis]}")
                    print('-' * 50)
                    return reverse_district[province][dis]
            return district_value
        return None

def standardize_ward(row):
        ward_value = row['Xã/Phường/Thị trấn']

        def matching(ward_value, district_value, province_value):
            # Function to match values with its corresponding prefixes
            try:
                if ward_value in reverse_ward[province_value][district_value].keys():
                    return reverse_ward[province_value][district_value][ward_value]
            except:
                print(f'Ward value: {ward_value}\nDistrict value: {district_value}\nProvince value: {province_value}')
                print('-'*50)
                return None
            for ward in reverse_ward[province_value][district_value].keys():
                similarity = fuzz.ratio(ward_value, ward)
                if similarity >= 66:
                    return reverse_ward[province_value][district_value][ward]
                
        if ward_value:
            prefix = ['Xã', 'Phường', 'Thị trấn', 'Thị Trấn']
            for pre in prefix:
                if ward_value.startswith(pre):
                    return ward_value
            ward_value = normalize('NFC', ward_value)
            province_value = row['Tỉnh/Thành phố']
            district_value = row['Thành phố/Quận/Huyện/Thị xã']
            return matching(ward_value, district_value, province_value)
        else:
            short_add_value = row['short_address']
            if isinstance(short_add_value, str) and short_add_value != '':
                short_add_list = row['short_address'].split(',')
                if len(short_add_list) >= 3:
                    new_province_val = row['Tỉnh/Thành phố']
                    new_ward_val = normalize('NFC',short_add_list[-3].strip())
                    new_district_val = row['Thành phố/Quận/Huyện/Thị xã']
                    return matching(new_ward_val, new_district_val, new_province_val)
            return None


# cleaned['ward'] = cleaned.apply(standardize_ward, axis=1)

# Test Ward

In [ ]:
from unicodedata import normalize
import re

def standardize_ward(row):
        ward_value = row['Xã/Phường/Thị trấn']

        def matching(ward_value, district_value, province_value):
            # Function to match values with its corresponding prefixes
            if ward_value in reverse_ward[province_value][district_value].keys():
                return reverse_ward[province_value][district_value][ward_value]
            for ward in reverse_ward[province_value][district_value].keys():
                similarity = fuzz.ratio(ward_value, ward)
                if similarity >= 66:
                    return reverse_ward[province_value][district_value][ward]
            return None
                
        if ward_value:
            prefix = ['Xã', 'Phường', 'Thị trấn', 'Thị Trấn']
            for pre in prefix:
                if ward_value.startswith(pre):
                    return ward_value
            ward_value = normalize('NFC', ward_value)
            province_value = row['Tỉnh/Thành phố']
            district_value = row['Thành phố/Quận/Huyện/Thị xã']
            return matching(ward_value, district_value, province_value)
        else:
            short_add = row['short_address']
            if isinstance(short_add, str) and short_add != '':
                if 'xã' in short_add.lower():
                    print(f"Xã in short_add: {short_add.lower()}")
                    match_result = re.search(pattern='(xã [\w\s]+)', string=short_add.lower())
                    if match_result:
                        match_result = match_result[0]
                        result_split = match_result.split()
                        result = ' '.join(i.capitalize() for i in result_split)
                        return result
                elif 'phường' in short_add.lower():
                    print(f'Phường in short_add: {short_add.lower()}')
                    match_result = re.search(pattern='(phường [\w\s]+)', string=short_add.lower())
                    if match_result:
                        match_result = match_result[0]
                        result_split = match_result.split()
                        result = ' '.join(i.capitalize() for i in result_split)
                        return result
                elif 'thị trấn' in short_add.lower():
                    print(f'Thị trấn in short_add: {short_add.lower()}')
                    match_result = re.search(pattern='(thị trấn [\w\s]+)', string=short_add.lower())
                    if match_result:
                        match_result = match_result[0]
                        result_split = match_result.split()
                        result = ' '.join(i.capitalize() for i in result_split)
                        return result
                else:
                    short_add_list = row['short_address'].split(',')
                    if len(short_add_list) >= 3:
                        new_province_val = row['Tỉnh/Thành phố']
                        new_ward_val = normalize('NFC',short_add_list[-3].strip())
                        new_district_val = row['Thành phố/Quận/Huyện/Thị xã']
                        return matching(new_ward_val, new_district_val, new_province_val)

            else:
                return None
                # short_add_list = row['short_address'].split(',')
                # if len(short_add_list) >= 3:
                #     new_province_val = row['Tỉnh/Thành phố']
                #     new_ward_val = normalize('NFC',short_add_list[-3].strip())
                #     new_district_val = row['Thành phố/Quận/Huyện/Thị xã']
                #     return matching(new_ward_val, new_district_val, new_province_val)
            return None

In [ ]:
from rapidfuzz import fuzz

yo = cleaned['district'].iloc[24895]
dis = list(reverse_district['Tỉnh Đắk Lắk'].keys())[4]
print(fuzz.ratio(yo, dis))

66.66666666666667


# Test Prices (Mức giá)

In [ ]:
import pandas as pd
import numpy as np

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls'], axis=1, inplace=True)
cleaned.rename(columns={"Nguồn thông tin": 'url'}, inplace=True)

df = pd.merge(left=cleaned, right=listing_details, how='left', on='url')
df.info()

In [ ]:
import json

df['other_info'] = df['other_info'].apply(json.loads)
df['price'] = df['other_info'].apply(lambda x: x.get('Mức giá'))

check_price_df = df[~df['price'].str.contains('tỷ', na=False)]
check_price_df = check_price_df[~(check_price_df['price'] == 'Thỏa thuận')]
print(f'Shape: {check_price_df.shape}')

check_price_df.dropna(subset = 'price', inplace=True, axis=0)
check_price_df['digit_price'] = check_price_df['price'].apply(lambda x: x.split()[0].replace(',', '.').strip())
check_price_df['digit_price'] = check_price_df['digit_price'].astype(float)
check_price_df['unit_price'] = check_price_df['price'].apply(lambda x: x.split()[1].strip())
print(check_price_df['unit_price'].unique())

nghin_met_vuong = check_price_df[check_price_df['unit_price'] == 'nghìn/m²']
nghin = check_price_df[check_price_df['unit_price'] == 'nghìn']
trieu_met_vuong = check_price_df[check_price_df['unit_price'] == 'triệu/m²']
trieu_incorrect = check_price_df[(check_price_df['unit_price'] == 'triệu') & (check_price_df['digit_price'] <= 300)]

# Test Khoảng cách tới trục đường chính

In [2]:
import pandas as pd
import numpy as np
import json

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls', 'description'], axis=1, inplace=True)
cleaned.rename(columns={"Nguồn thông tin": 'url'}, inplace=True)

df = pd.merge(left=cleaned, right=listing_details, how='left', on='url')
df['other_info'] = df['other_info'].apply(json.loads)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27491 entries, 0 to 27490
Data columns (total 35 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Tỉnh/Thành phố                        27491 non-null  object 
 1   Thành phố/Quận/Huyện/Thị xã           27491 non-null  object 
 2   Xã/Phường/Thị trấn                    27469 non-null  object 
 3   Đường phố                             23802 non-null  object 
 4   Chi tiết                              27491 non-null  object 
 5   url                                   27491 non-null  object 
 6   Tình trạng giao dịch                  27491 non-null  object 
 7   Thời điểm giao dịch/rao bán           27479 non-null  object 
 8   Thông tin liên hệ                     0 non-null      object 
 9   Giá rao bán/giao dịch                 24953 non-null  float64
 10  Loại đơn giá (đ/m2 hoặc đ/m ngang)    27491 non-null  object 
 11  Số tầng công tr

In [3]:
df['Đường vào'] = df['other_info'].apply(lambda x: x.get('Đường vào'))

In [8]:
df.dropna(subset='Đường vào', axis=0, inplace=True)
df['digit_road'] = df['Đường vào'].apply(lambda x: x.split()[0].replace(',', '.').strip() if x is not None else None)
df['digit_road'] = df['digit_road'].astype(float)

- Không có trong description: 54, 152, 261, 433, 480, 642, 779, 798, 1176, 1181, 1199, 1364, 1405, 1829, 1967, 2199, 2333, 2391, 2435, 2733, 2797m, 2822, 3026, 3038, 3145, 3335, 3383, 3398, 3440, 3512, 3520, 3566, 3669, 3728, 3834, 3900, 3981, 4335, 4584, 4659, 4704, 4762, 4869, 4883, 4950, 5217, 5225, 5404, 5480, 5568, 5648, 5771, 5818, 5987, 5988,...

- Đúng là độ rộng ngõ ngách nhỏ nhất: 135, 319, 1619, 1824, 1962, 2016, 2439, 2532, 2791, 2933, 2988, 3050, 3134, 3142, 3177, 3300, 3367, 3803, 4442, 5387, 5525, 5547, 5724, 6164, 6377, 6699, 6714, 6722, 7029, 8197, 8207, 9092, 9217, 9243, 9336, 10138, 10719, 10998, 11067

- Khoảng cách tới trục đường chính:
    - 1988 (40 m): Hẻm ba gác cách mặt tiền 30m
    - 6969 (50 m): Nhà cách mặt phố Thái Hà 50m, ngõ rộng 5m
    - 7053 (20 m): cách mặt phố 20m

- Khác:
    - 410 (50 m): cách bãi gửi ô tô chỉ 50m 
    - 726 (17 m): Lộ giới: 16m
    - 1622 (30 m): Đường trước nhà 4m xe hơi

- Sai: 
    - 1956 (40m): Hẻm trước nhà 4m
    - 2623 (150 m): Hẻm 5m xe hơi đậu trước nhà
    - 2913 (30 m): Khoảng sân trước 30m tiện kinh doanh mua bán
    - 3312 (200 m): Ngõ rộng 200cm
    - 3374 (50 m): Đường trước nhà 10m Xe hơi vào tận cửa
    - 3375 (50 m): Đường nhựa 10m Xe hơi ra vào thoải mái
    - 3379 (20 m): Đường xe hơi 8m thông thoáng khu vực văn minh
    - 5601 (20 m - khoảng cách tới trục đường chính): Đường trước nhà 4m
    - 6969 (50 m): Nhà cách mặt phố Thái Hà 50m, ngõ rộng 5m
    - 7900 (30 m): Hẻm nhựa 7m xe hơi tận nhà
    - 8521 (22 m): Chính chủ gửi bán căn nhà phố trục chính đường 22m
    - 8692 (60 m): HẺM XE HƠI\nCách mặt tiền chỉ 60m
    - 9268 (17 m): Đường trước nhà 17m. Vỉa hè 3m
    - 9788 (18 m): Mặt tiền đường lớn
    - 9804 (100 m): Hẻm trước nhà 4m
    - 9974 (20 m): mặt tiền đường 20m
    - 10186 (30 m): Đường rộng 30m
    - 10239 (20 m): Tọa lạc tại phố Lê Đức Thọ
    - 10247 + 10251 (16 m): Đường trước nhà: 16m
    - 10448 (20 m): hẻm 10m
    - 10477 (25 m): Đường trước nhà
    - 10566 (24 m): đường trước nhà 24m chạy thẳng ra biển
    - 10654 (16 m): Đường rộng 6m xe tải vào nhà
    - 10746 (16 m): góc đường Thân Văn Nhiếp
    - 10870 (150 m): Ngõ rộng 150, thuận tiện cho xe hơi vào


Đã làm tới số 11067


In [17]:
df.loc[9268]['url']

'https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-chanh-phuong-yen-hoa-2/chinh-chu-ban-khu-pho-mac-thai-to-pr42934241'

In [14]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

df[df['digit_road'] > 15][['Đường vào', 'description']]

Đường vào  \
54         70 m   
135        16 m   
152        20 m   
261        20 m   
319        20 m   
410        50 m   
433        30 m   
480        20 m   
642       160 m   
726        17 m   
779        20 m   
798        20 m   
1176       22 m   
1181       20 m   
1199       21 m   
1364       17 m   
1405       30 m   
1619       16 m   
1622       30 m   
1824       16 m   
1829       30 m   
1956       40 m   
1962       30 m   
1967       30 m   
1988       40 m   
2016       40 m   
2199       20 m   
2333       16 m   
2391       30 m   
2435       18 m   
2439       26 m   
2532       20 m   
2623      150 m   
2733       20 m   
2791       20 m   
2797       20 m   
2822       17 m   
2913       30 m   
2933       20 m   
2988       20 m   
3026       20 m   
3038       20 m   
3050       16 m   
3134       16 m   
3142       20 m   
3145       20 m   
3177       20 m   
3300       20 m   
3312      200 m   
3335       25 m   
3367       16 m   
3374       50 m   
3375       50 m   
3379       20 m   
3383       20 m   
3398       22 m   
3440       22 m   
3512       30 m   
3520       20 m   
3566       21 m   
3669       20 m   
3728       16 m   
3803       24 m   
3834     17,5 m   
3900       35 m   
3981       18 m   
4046       40 m   
4335       18 m   
4442       20 m   
4584       20 m   
4659       20 m   
4704       50 m   
4762       20 m   
4869       30 m   
4883       20 m   
4950       20 m   
5217       20 m   
5225       60 m   
5387       16 m   
5404       20 m   
5480       20 m   
5525       20 m   
5547       20 m   
5568       18 m   
5601       20 m   
5648       18 m   
5724       20 m   
5771       16 m   
5807       16 m   
5818       25 m   
5987       20 m   
5988       16 m   
6041       20 m   
6087       20 m   
6164       20 m   
6173       25 m   
6189       16 m   
6214       30 m   
6305       16 m   
6377       20 m   
6658       36 m   
6699       20 m   
6714       30 m   
6722       40 m   
6727       16 m   
6940       50 m   
6969       50 m   
7029       25 m   
7053       20 m   
7067       20 m   
7072       20 m   
7073       19 m   
7096       20 m   
7100       16 m   
7391     19,5 m   
7493      100 m   
7525       40 m   
7617       20 m   
7635       20 m   
7846       20 m   
7900       30 m   
7953       50 m   
7969      100 m   
8069       18 m   
8155       20 m   
8180       20 m   
8197       20 m   
8207       24 m   
8230       20 m   
8503       30 m   
8521       22 m   
8692       60 m   
8718       20 m   
8755       50 m   
8882       20 m   
8945       20 m   
9015       30 m   
9037       20 m   
9092       16 m   
9208       30 m   
9217       16 m   
9243       20 m   
9268       17 m   
9276       18 m   
9336       25 m   
9383       19 m   
9436       20 m   
9586       50 m   
9788       18 m   
9804      100 m   
9974       20 m   
10020      20 m   
10093      30 m   
10138      16 m   
10186      30 m   
10239      20 m   
10247      16 m   
10251      16 m   
10418      30 m   
10448      20 m   
10477      25 m   
10566      24 m   
10654      16 m   
10719      20 m   
10746      16 m   
10755      16 m   
10850      20 m   
10870     150 m   
10998      16 m   
11067      16 m   
11081      24 m   
11114      16 m   
11338      16 m   
11398      25 m   
11453     100 m   
11527      20 m   
11649      20 m   
11652      20 m   
11662      20 m   
11703      16 m   
11731      30 m   
11734      50 m   
11774      20 m   
11950      30 m   
11959      23 m   
12049      24 m   
12110     150 m   
12191      16 m   
12195      16 m   
12199      30 m   
12237      20 m   
12263      20 m   
12292      30 m   
12422      20 m   
12469    17,5 m   
12533      32 m   
12662      27 m   
12812      20 m   
12901      16 m   
12958      80 m   
13004      20 m   
13024      22 m   
13261      20 m   
13263      20 m   
13420      30 m   
13522      20 m   
13529      20 m   
13612      20 m   
13616      20 m   
13799      16 m 